# Pommerman Demo.

This notebook demonstrates how to train Pommerman agents. Please let us know at support@pommerman.com if you run into any issues.

In [74]:
import os
import sys
import numpy as np
import time
import itertools
import random

import pommerman
from pommerman.agents import SimpleAgent, RandomAgent, PlayerAgent, BaseAgent, SmartRandomAgent, StaticAgent, SmartRandomAgentNoBomb
from pommerman.configs import ffa_v0_fast_env, lesson1_env, lesson2_env, lesson2b_env, lesson2c_env, lesson2d_env, lesson2e_env, lesson3_env, lesson3b_env, lesson3c_env, lesson3d_env, ffa_v4_fast_env
from pommerman.envs.v0 import Pomme as Pomme_v0
from pommerman.envs.v4 import Pomme as Pomme_v4
from pommerman.characters import Bomber
from pommerman import utility
from pommerman import agents
from pommerman import envs
from pommerman import constants
from pommerman import characters

# print all env configs
print(pommerman.REGISTRY)

['AdvancedLesson-v0', 'PommeFFACompetition-v0', 'PommeFFACompetitionFast-v0', 'PommeFFAFast-v0', 'PommeFFA-v1', 'PommeFFAFast-v3', 'PommeFFAFast-v4', 'Lesson1-v0', 'Lesson2-v0', 'Lesson2b-v0', 'Lesson2c-v0', 'Lesson2d-v0', 'Lesson2e-v0', 'Lesson3-v0', 'Lesson3b-v0', 'Lesson3c-v0', 'Lesson3d-v0', 'OneVsOne-v0', 'PommeRadioCompetition-v2', 'PommeRadio-v2', 'Simple-v0', 'SimpleRandomTeam-v0', 'SimpleTeam-v0', 'PommeTeamCompetition-v0', 'PommeTeamCompetitionFast-v0', 'PommeTeamCompetition-v1', 'PommeTeam-v0', 'PommeTeamFast-v0', 'PommeTeamSimple-v0']


# Train with stable baseline

In [2]:
import gym

from stable_baselines.common.policies import MlpPolicy, CnnLstmPolicy, MlpLstmPolicy
from stable_baselines.common.vec_env import SubprocVecEnv, DummyVecEnv
from stable_baselines import PPO2

The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
  * https://github.com/tensorflow/io (for I/O related ops)
If you depend on functionality not listed there, please file an issue.



## Inherit pommerman env and make it compatible with stable-baseline

In [87]:
class CustomPomme(Pomme_v0):
    def __init__(self, **kwargs):
        super().__init__(**kwargs)
        self.obs_raw = None # store the raw version of observation
        self.training_idx = 1 # idx of the agent being trained
        self.time_step_reward = kwargs["time_step_reward"] # reward for each time step
        self.wood_reward = kwargs["wood_reward"] # reward for destroying each box
        
    
    # function to flatten pommerman observation
    def _transform_obs(self, obs_raw):
        obs_training = obs_raw[self.training_idx] # default the first agent to be trained

        # construct flattened observation
        obs = [
            *np.array(obs_training["board"]).reshape(-1),
            *np.array(obs_training["bomb_blast_strength"]).reshape(-1),
            *np.array(obs_training["bomb_life"]).reshape(-1),
            *np.array(obs_training["position"]).reshape(-1),
            obs_training["ammo"],
            obs_training["blast_strength"],
            obs_training["can_kick"],
            obs_training["teammate"].value,
            obs_training["enemies"][0].value,
            
            # uncommon if training 1 v 1
            obs_training["enemies"][0].value,
            obs_training["enemies"][0].value,
            
            # uncommon if training 2 v 2
#             obs_training["enemies"][1].value,
#             obs_training["enemies"][2].value,
        ]
        return obs
    
    # count the number of all elements in an np array
    def _ele_counter(self, a):
        unique, counts = np.unique(a, return_counts=True)
        return dict(zip(unique, counts))
    
    def get_obs_raw(self):
        return self.obs_raw

    def step(self, action_training):
        # obtain action of oponent agents
        action_nontraining = self.act(self.obs_raw)
        
        # combine actions
        actions = [*action_nontraining, action_training]
        
        # step
        obs_raw, reward, done, info = super().step(actions)
        reward_training = reward[self.training_idx]
        self.obs_raw = obs_raw

        #######################################################################################################
        ### tweak reward system for wooden box collecting problem, comment if training for original problem ###
        
        obs_training = obs_raw[self.training_idx]
#         display(obs_training)
        
        # count number of wood
        board = np.array(obs_training["board"])
        ele_count = self._ele_counter(board)
        curr_num_wood = 0
        if 2 in ele_count:
            curr_num_wood = ele_count[2] # number of wood in current time step, 2 represents wood
        
        # calculate reward
        time_step = obs_training["step_count"] # number of time step in a single game
        reward_training += (self._num_wood - curr_num_wood) * self.wood_reward + time_step * self.time_step_reward
        
        # if the game end with tie, gives -1 reward
        if "result" in info:
            if(info["result"].value == 2):
                reward_training += -1
            
#         print("reward_training = (self._num_wood - curr_num_wood) * self.wood_reward + time_step * self.time_step_reward: ")
#         print(reward_training, " = (", self._num_wood, " - ", curr_num_wood, ")", " * ", self.wood_reward, " + ", time_step, " * ", self.time_step_reward)
#         print()
        #######################################################################################################
        
        return self._transform_obs(obs_raw), reward_training, done, info
    
    def reset(self):
        obs_raw = super().reset()
        self.obs_raw = obs_raw
        return self._transform_obs(obs_raw)
    
    def render(self,
               mode=None,
               close=False,
               record_pngs_dir=None,
               record_json_dir=None,
               do_sleep=True):
        super().render(mode=mode,
                       close=close,
                       record_pngs_dir=record_pngs_dir,
                       record_json_dir=record_json_dir,
                       do_sleep=do_sleep)

## Custom CNN Policy

In [88]:
import tensorflow as tf

from stable_baselines.a2c.utils import linear
from stable_baselines.common.policies import ActorCriticPolicy

class CustomCNN(ActorCriticPolicy):
    def __init__(self, sess, ob_space, ac_space, n_env, n_steps, n_batch, reuse=False, **kwargs):
        super(CustomCNN, self).__init__(sess, ob_space, ac_space, n_env, n_steps, n_batch, reuse=reuse)
        size=11
        bp = 3*size**2 #board partition
        with tf.variable_scope("model", reuse=reuse):
            obs = self.processed_obs
            self.board1, self.misc = tf.split(obs, [bp, -1], 1)
            
            self.board = tf.reshape(self.board1, (-1, size, size, 3))
            self.conv1 = tf.layers.conv2d(self.board, 64, 2, activation=tf.nn.relu, name='conv1')
            self.conv2 = tf.layers.conv2d(self.conv1, 32, 2, activation=tf.nn.relu, name='conv2')
            self.fc0 = tf.contrib.layers.flatten(self.conv2)
            self.fc1 = tf.concat((self.fc0, self.misc), -1)
            self.fc1 = tf.layers.dense(self.fc1, 1024, name = 'fc1')
            self.actions = tf.layers.dense(self.fc1, 6)   
            self.valueUM = tf.layers.dense(self.fc1, 128) #??

            self._proba_distribution, self._policy, self.q_value = \
                self.pdtype.proba_distribution_from_latent(self.actions, self.valueUM, init_scale=0.01)

        self._value_fn = linear(self.valueUM, 'vf', 1)
        self._setup_init()

    def step(self, obs, state=None, mask=None, deterministic=False):
        if deterministic:
            action, value, neglogp = self.sess.run([self.deterministic_action, self.value_flat, self.neglogp],
                                                   {self.obs_ph: obs})
        else:
            action, value, neglogp = self.sess.run([self.action, self.value_flat, self.neglogp],
                                                   {self.obs_ph: obs})
        return action, value, self.initial_state, neglogp

    def proba_step(self, obs, state=None, mask=None):
        return self.sess.run(self.policy_proba, {self.obs_ph: obs})

    def value(self, obs, state=None, mask=None):
        return self.sess.run(self.value_flat, {self.obs_ph: obs})

## Demo envs

In [89]:
def team_v3_fast_env():
    """Start up a FFA config with the default settings."""
    env = CustomPomme
    game_type = constants.GameType.Team
    env_entry_point = 'CustomPomme'
    env_id = 'PommeTeamFast-v3'
    env_kwargs = {
        'game_type': game_type,
        'board_size': 8,
        'num_rigid': 0,
        'num_wood': 0,
        'num_items': 0,
        'max_steps': constants.MAX_STEPS,
        'render_fps': 1000,
        'env': env_entry_point,
        "wood_reward": 0.01, # added for box collecting env
        "time_step_reward": -0.001, # added for box collecting env
        "rand_agent_pos": True # randomize initial position of agent
    }
    agent = characters.Bomber
    return locals()

def one_vs_one_v3_env():
    """Start up a FFA config with the default settings."""
    env = CustomPomme
    game_type = constants.GameType.OneVsOne
    env_entry_point = 'CustomPomme'
    env_id = 'PommeOneVsOneFast-v3'
    env_kwargs = {
        'game_type': game_type,
        'board_size': 8,
        'num_rigid': 0,
        'num_wood': 0,
        'num_items': 0,
        'max_steps': constants.MAX_STEPS,
        'render_fps': 1000,
        'env': env_entry_point,
        "wood_reward": 0.01, # added for box collecting env
        "time_step_reward": -0.001, # added for box collecting env
        "rand_agent_pos": True # randomize initial position of agent
    }
    agent = characters.Bomber
    return locals()

def one_vs_one_v4_env():
    """Start up a FFA config with the default settings."""
    env = CustomPomme
    game_type = constants.GameType.OneVsOne
    env_entry_point = 'CustomPomme'
    env_id = 'PommeOneVsOneFast-v4'
    env_kwargs = {
        'game_type': game_type,
        'board_size': 8,
        'free_board_size': constants.FREE_BOARD_SIZE,
        'num_rigid': 0,
        'num_wood': 0,
        'num_items': 0,
        'max_steps': constants.MAX_STEPS,
        'render_fps': 1000,
        'env': env_entry_point,
        "wood_reward": 0.01, # added for box collecting env
        "time_step_reward": -0.001, # added for box collecting env
        "rand_agent_pos": True # randomize initial position of agent
    }
    agent = characters.Bomber
    return locals()

## Wooden Box collecting curriculum training envs

In [90]:
env_num_woods = [8, 10, 12, 14, 16, 18] # number of woods for lesson 0, 1, 2, 3, 4, 5
# env_wood_reward = [pow(2, i) for i in range(-1, -7, -1)] # reward for destroying each box
env_wood_reward = [0.1/x for x in env_num_woods] # reward for destroying each box
board_size = 11

def wood_box_lesson0_env():
    """Start up a FFA config with the default settings."""
    env = CustomPomme
    game_type = constants.GameType.OneVsOne
    env_entry_point = 'CustomPomme'
    env_id = 'WoodBoxLesson0'
    env_kwargs = {
        'game_type': game_type,
        'board_size': board_size,
        'free_board_size': constants.FREE_BOARD_SIZE,
        'num_rigid': 0,
        'num_wood': env_num_woods[0],
        'num_items': 0,
        'max_steps': constants.MAX_STEPS,
        'render_fps': 1000,
        'env': env_entry_point,
        "wood_reward": env_wood_reward[0], # added for box collecting env
        "time_step_reward": -0.001, # added for box collecting env
        "rand_agent_pos": True # randomize initial position of agent
    }
    agent = characters.Bomber
    return locals()

def wood_box_lesson1_env():
    """Start up a FFA config with the default settings."""
    env = CustomPomme
    game_type = constants.GameType.OneVsOne
    env_entry_point = 'CustomPomme'
    env_id = 'WoodBoxLesson1'
    env_kwargs = {
        'game_type': game_type,
        'board_size': board_size,
        'free_board_size': constants.FREE_BOARD_SIZE,
        'num_rigid': 0,
        'num_wood': env_num_woods[1],
        'num_items': 0,
        'max_steps': constants.MAX_STEPS,
        'render_fps': 1000,
        'env': env_entry_point,
        "wood_reward": env_wood_reward[1], # added for box collecting env
        "time_step_reward": -0.001, # added for box collecting env
        "rand_agent_pos": True # randomize initial position of agent
    }
    agent = characters.Bomber
    return locals()

def wood_box_lesson2_env():
    """Start up a FFA config with the default settings."""
    env = CustomPomme
    game_type = constants.GameType.OneVsOne
    env_entry_point = 'CustomPomme'
    env_id = 'WoodBoxLesson2'
    env_kwargs = {
        'game_type': game_type,
        'board_size': board_size,
        'free_board_size': constants.FREE_BOARD_SIZE,
        'num_rigid': 0,
        'num_wood': env_num_woods[2],
        'num_items': 0,
        'max_steps': constants.MAX_STEPS,
        'render_fps': 1000,
        'env': env_entry_point,
        "wood_reward": env_wood_reward[2], # added for box collecting env
        "time_step_reward": -0.001, # added for box collecting env
        "rand_agent_pos": True # randomize initial position of agent
    }
    agent = characters.Bomber
    return locals()

def wood_box_lesson3_env():
    """Start up a FFA config with the default settings."""
    env = CustomPomme
    game_type = constants.GameType.OneVsOne
    env_entry_point = 'CustomPomme'
    env_id = 'WoodBoxLesson3'
    env_kwargs = {
        'game_type': game_type,
        'board_size': board_size,
        'free_board_size': constants.FREE_BOARD_SIZE,
        'num_rigid': 0,
        'num_wood': env_num_woods[3],
        'num_items': 0,
        'max_steps': constants.MAX_STEPS,
        'render_fps': 1000,
        'env': env_entry_point,
        "wood_reward": env_wood_reward[3], # added for box collecting env
        "time_step_reward": -0.001, # added for box collecting env
        "rand_agent_pos": True # randomize initial position of agent
    }
    agent = characters.Bomber
    return locals()

def wood_box_lesson4_env():
    """Start up a FFA config with the default settings."""
    env = CustomPomme
    game_type = constants.GameType.OneVsOne
    env_entry_point = 'CustomPomme'
    env_id = 'WoodBoxLesson4'
    env_kwargs = {
        'game_type': game_type,
        'board_size': board_size,
        'free_board_size': constants.FREE_BOARD_SIZE,
        'num_rigid': 0,
        'num_wood': env_num_woods[4],
        'num_items': 0,
        'max_steps': constants.MAX_STEPS,
        'render_fps': 1000,
        'env': env_entry_point,
        "wood_reward": env_wood_reward[4], # added for box collecting env
        "time_step_reward": -0.001, # added for box collecting env
        "rand_agent_pos": True # randomize initial position of agent
    }
    agent = characters.Bomber
    return locals()

def wood_box_lesson5_env():
    """Start up a FFA config with the default settings."""
    env = CustomPomme
    game_type = constants.GameType.OneVsOne
    env_entry_point = 'CustomPomme'
    env_id = 'WoodBoxLesson5'
    env_kwargs = {
        'game_type': game_type,
        'board_size': board_size,
        'free_board_size': constants.FREE_BOARD_SIZE,
        'num_rigid': 0,
        'num_wood': env_num_woods[5],
        'num_items': 0,
        'max_steps': constants.MAX_STEPS,
        'render_fps': 1000,
        'env': env_entry_point,
        "wood_reward": env_wood_reward[5], # added for box collecting env
        "time_step_reward": -0.001, # added for box collecting env
        "rand_agent_pos": True # randomize initial position of agent
    }
    agent = characters.Bomber
    return locals()

In [91]:
# log function during training, implement if needed
def log(local_var, global_var):
    pass
#     display(local_var)
#     display(global_var)

# number of cpu
n_cpu = 1

# env initialization

In [92]:
def initialize_env(config):
    env_pom = CustomPomme(**config["env_kwargs"])

    # config agents
    agents = []

    # Add opponent agents
    for agent_id in range(1):
        agents.append(StaticAgent(config["agent"](agent_id, config["game_type"])))

    # add player agent(to train)
    agents.append(PlayerAgent(config["agent"](1, config["game_type"])))

    env_pom.set_agents(agents)
    env_pom.set_training_agent(agents[1].agent_id)
    env_pom.set_init_game_state(None)

    # Seed and reset the environment
    env_pom.seed(0)
    
    # set up env vector
    env = DummyVecEnv([lambda: env_pom for i in range(n_cpu)])
    
    return env


def initialize_env_smart_random(config):
    env_pom = CustomPomme(**config["env_kwargs"])

    # config agents
    agents = []

    # Add opponent agents
    for agent_id in range(1):
        agents.append(SmartRandomAgentNoBomb(config["agent"](agent_id, config["game_type"])))

    # add player agent(to train)
    agents.append(PlayerAgent(config["agent"](1, config["game_type"])))

    env_pom.set_agents(agents)
    env_pom.set_training_agent(agents[1].agent_id)
    env_pom.set_init_game_state(None)

    # Seed and reset the environment
    env_pom.seed(0)
    
    # set up env vector
    env = DummyVecEnv([lambda: env_pom for i in range(n_cpu)])
    
    return env


def initialize_env_simple(config):
    env_pom = CustomPomme(**config["env_kwargs"])

    # config agents
    agents = []

    # Add opponent agents
    for agent_id in range(1):
        agents.append(SimpleAgent(config["agent"](agent_id, config["game_type"])))

    # add player agent(to train)
    agents.append(PlayerAgent(config["agent"](1, config["game_type"])))

    env_pom.set_agents(agents)
    env_pom.set_training_agent(agents[1].agent_id)
    env_pom.set_init_game_state(None)

    # Seed and reset the environment
    env_pom.seed(0)
    
    # set up env vector
    env = DummyVecEnv([lambda: env_pom for i in range(n_cpu)])
    
    return env

# Training loop

In [93]:
def train(model_name, model = None, env = None, n_steps=2400, total_timesteps=50000):
    if model == None:
        model = PPO2(#MlpPolicy,
                     CustomCNN,
                     #CnnLstmPolicy,
                     #MlpLstmPolicy,
                     env, 
                     verbose=1, 
                     n_steps = n_steps, # batch_size = n_step * num_env
                     ent_coef = 0.001, # entropy coefficient
                     nminibatches = 1,
                     tensorboard_log = "./ppo2_pommerman_box_collect_tensorboard_version4/")
    else:
        model.set_env(env)
    model = model.learn(total_timesteps = total_timesteps, # num_update = total_timesteps // batch_size
                        callback = log, tb_log_name = model_name)
    return model

# Testing loop

In [94]:
def test(env, model, render=False, total = 100):
    # test the learned model
    num_win = 0
    num_tie = 0
    num_lose = 0
    total = total # number of playouts
    for i_episode in range(total):
        obs = env.reset()
        done = False
        info = None
        while not done:
            if render:
                env.render()
                time.sleep(0.1)
            action_training, _states = model.predict(obs)
    #         print(action_training)
            obs, rewards, dones, infos = env.step(action_training)
    #         print(infos)
            done = dones[0]
            info = infos[0]
        print('Episode {} finished'.format(i_episode))
        if(info["result"].value == 0):
            if(1 in info["winners"]):
                num_win+=1
            else:
                num_lose+=1
        elif(info["result"].value == 2):
            num_tie+=1
    #     print(info)
    env.close()
    print("Win ", num_win, "/", total, " games")
    print("Tie ", num_tie, "/", total, " games")
    print("Lose ", num_lose, "/", total, " games")

# Training Lessons

## useful constants

In [95]:
total_timestep = 5000000
n_steps = 3200

## Training lesson 0.
### 11x11 grid with 2 wooden boxes

In [96]:
config_lesson0 = wood_box_lesson0_env()
env_lesson0 = initialize_env(config_lesson0)
model_names = ["wooden_box_collecting_lesson" + str(x) + "_agent_" + str(total_timestep) + "_" + str(n_steps) + "_" + "customCNN" for x in range(6)]

In [97]:
model_lesson0 = train(model_name = model_names[0], 
                      env = env_lesson0, 
                      n_steps = n_steps, 
                      total_timesteps=total_timestep)
# model_lesson0.save(model_names[0])

## Testing lesson0

In [56]:
# model_lesson0 = PPO2.load(model_names[0])
test(env_lesson0, model_lesson0, render = False)

Episode 0 finished
Episode 1 finished
Episode 2 finished
Episode 3 finished
Episode 4 finished
Episode 5 finished
Episode 6 finished
Episode 7 finished
Episode 8 finished
Episode 9 finished
Episode 10 finished
Episode 11 finished
Episode 12 finished
Episode 13 finished
Episode 14 finished
Episode 15 finished
Episode 16 finished
Episode 17 finished
Episode 18 finished
Episode 19 finished
Episode 20 finished
Episode 21 finished
Episode 22 finished
Episode 23 finished
Episode 24 finished
Episode 25 finished
Episode 26 finished
Episode 27 finished
Episode 28 finished
Episode 29 finished
Episode 30 finished
Episode 31 finished
Episode 32 finished
Episode 33 finished
Episode 34 finished
Episode 35 finished
Episode 36 finished
Episode 37 finished
Episode 38 finished
Episode 39 finished
Episode 40 finished
Episode 41 finished
Episode 42 finished
Episode 43 finished
Episode 44 finished
Episode 45 finished
Episode 46 finished
Episode 47 finished
Episode 48 finished
Episode 49 finished
Episode 50

## Training lesson 1
### 11x11 grid with 4 wooden boxes

In [57]:
config_lesson1 = wood_box_lesson1_env()
env_lesson1 = initialize_env(config_lesson1)

In [58]:
# model_lesson0 = PPO2.load(load_path = model_names[0],
#                           tensorboard_log = "./ppo2_pommerman_box_collect_tensorboard/")
model_lesson1 = train(model_name = model_names[1], 
                      model = model_lesson0,
                      env = env_lesson1, 
                      n_steps = n_steps, 
                      total_timesteps = total_timestep)
# model_lesson1.save(model_names[1])

--------------------------------------
| approxkl           | 0.0004900428  |
| clipfrac           | 0.0061718747  |
| explained_variance | 0.215         |
| fps                | 1037          |
| n_updates          | 1             |
| policy_entropy     | 0.07649745    |
| policy_loss        | 0.00032511554 |
| serial_timesteps   | 3200          |
| time_elapsed       | 2.86e-06      |
| total_timesteps    | 3200          |
| value_loss         | 14.374535     |
--------------------------------------
---------------------------------------
| approxkl           | 0.00034197408  |
| clipfrac           | 0.004296875    |
| explained_variance | 0.337          |
| fps                | 1007           |
| n_updates          | 2              |
| policy_entropy     | 0.10851507     |
| policy_loss        | -0.00029847547 |
| serial_timesteps   | 6400           |
| time_elapsed       | 3.09           |
| total_timesteps    | 6400           |
| value_loss         | 6.8523774      |
-------------

-------------------------------------
| approxkl           | 0.0048488276 |
| clipfrac           | 0.06304688   |
| explained_variance | 0.647        |
| fps                | 1025         |
| n_updates          | 18           |
| policy_entropy     | 0.24386092   |
| policy_loss        | 0.0035211197 |
| serial_timesteps   | 57600        |
| time_elapsed       | 52.9         |
| total_timesteps    | 57600        |
| value_loss         | 7.1207514    |
-------------------------------------
---------------------------------------
| approxkl           | 4.4805096e-05  |
| clipfrac           | 0.0            |
| explained_variance | 0.8            |
| fps                | 999            |
| n_updates          | 19             |
| policy_entropy     | 0.06684391     |
| policy_loss        | -0.00013610921 |
| serial_timesteps   | 60800          |
| time_elapsed       | 56             |
| total_timesteps    | 60800          |
| value_loss         | 8.7858305      |
--------------------------

---------------------------------------
| approxkl           | 4.5361216e-05  |
| clipfrac           | 0.0            |
| explained_variance | 0.765          |
| fps                | 1002           |
| n_updates          | 35             |
| policy_entropy     | 0.21924731     |
| policy_loss        | -2.4213641e-05 |
| serial_timesteps   | 112000         |
| time_elapsed       | 108            |
| total_timesteps    | 112000         |
| value_loss         | 9.220855       |
---------------------------------------
--------------------------------------
| approxkl           | 0.000544503   |
| clipfrac           | 7.8125e-05    |
| explained_variance | 0.789         |
| fps                | 992           |
| n_updates          | 36            |
| policy_entropy     | 0.16321927    |
| policy_loss        | 0.00013391607 |
| serial_timesteps   | 115200        |
| time_elapsed       | 111           |
| total_timesteps    | 115200        |
| value_loss         | 11.824411     |
------------

--------------------------------------
| approxkl           | 2.7710586e-05 |
| clipfrac           | 0.0           |
| explained_variance | 0.874         |
| fps                | 1017          |
| n_updates          | 51            |
| policy_entropy     | 0.052872054   |
| policy_loss        | 1.622919e-05  |
| serial_timesteps   | 163200        |
| time_elapsed       | 157           |
| total_timesteps    | 163200        |
| value_loss         | 7.7100234     |
--------------------------------------
--------------------------------------
| approxkl           | 3.6751167e-05 |
| clipfrac           | 0.0           |
| explained_variance | 0.888         |
| fps                | 1015          |
| n_updates          | 52            |
| policy_entropy     | 0.102970935   |
| policy_loss        | -7.694684e-05 |
| serial_timesteps   | 166400        |
| time_elapsed       | 160           |
| total_timesteps    | 166400        |
| value_loss         | 4.3985605     |
-------------------------

---------------------------------------
| approxkl           | 1.2602213e-05  |
| clipfrac           | 0.0            |
| explained_variance | 0.903          |
| fps                | 1049           |
| n_updates          | 68             |
| policy_entropy     | 0.04798369     |
| policy_loss        | -1.3240651e-05 |
| serial_timesteps   | 217600         |
| time_elapsed       | 210            |
| total_timesteps    | 217600         |
| value_loss         | 7.972863       |
---------------------------------------
--------------------------------------
| approxkl           | 7.5745935e-05 |
| clipfrac           | 0.0           |
| explained_variance | 0.875         |
| fps                | 997           |
| n_updates          | 69            |
| policy_entropy     | 0.08072549    |
| policy_loss        | 3.059745e-05  |
| serial_timesteps   | 220800        |
| time_elapsed       | 213           |
| total_timesteps    | 220800        |
| value_loss         | 8.532363      |
------------

...

--------------------------------------
| approxkl           | 0.00011402231 |
| clipfrac           | 0.001015625   |
| explained_variance | 0.888         |
| fps                | 1069          |
| n_updates          | 1486          |
| policy_entropy     | 0.12145337    |
| policy_loss        | 0.000291591   |
| serial_timesteps   | 4755200       |
| time_elapsed       | 4.77e+03      |
| total_timesteps    | 4755200       |
| value_loss         | 1.5265651     |
--------------------------------------
--------------------------------------
| approxkl           | 4.0615203e-05 |
| clipfrac           | 0.0           |
| explained_variance | 0.876         |
| fps                | 1122          |
| n_updates          | 1487          |
| policy_entropy     | 0.145332      |
| policy_loss        | -9.766034e-06 |
| serial_timesteps   | 4758400       |
| time_elapsed       | 4.78e+03      |
| total_timesteps    | 4758400       |
| value_loss         | 4.091963      |
-------------------------

--------------------------------------
| approxkl           | 0.00013026048 |
| clipfrac           | 0.001484375   |
| explained_variance | 0.901         |
| fps                | 1118          |
| n_updates          | 1503          |
| policy_entropy     | 0.074961826   |
| policy_loss        | -4.461769e-05 |
| serial_timesteps   | 4809600       |
| time_elapsed       | 4.82e+03      |
| total_timesteps    | 4809600       |
| value_loss         | 7.3271537     |
--------------------------------------
---------------------------------------
| approxkl           | 6.634187e-05   |
| clipfrac           | 0.000625       |
| explained_variance | 0.9            |
| fps                | 1131           |
| n_updates          | 1504           |
| policy_entropy     | 0.06671977     |
| policy_loss        | -0.00013344377 |
| serial_timesteps   | 4812800        |
| time_elapsed       | 4.83e+03       |
| total_timesteps    | 4812800        |
| value_loss         | 7.054882       |
-------------

---------------------------------------
| approxkl           | 0.00010538574  |
| clipfrac           | 7.8125e-05     |
| explained_variance | 0.914          |
| fps                | 1149           |
| n_updates          | 1520           |
| policy_entropy     | 0.17788324     |
| policy_loss        | -0.00047751443 |
| serial_timesteps   | 4864000        |
| time_elapsed       | 4.88e+03       |
| total_timesteps    | 4864000        |
| value_loss         | 3.7070453      |
---------------------------------------
--------------------------------------
| approxkl           | 0.00031351775 |
| clipfrac           | 0.0065625     |
| explained_variance | 0.918         |
| fps                | 1102          |
| n_updates          | 1521          |
| policy_entropy     | 0.19314174    |
| policy_loss        | 0.00022279247 |
| serial_timesteps   | 4867200       |
| time_elapsed       | 4.88e+03      |
| total_timesteps    | 4867200       |
| value_loss         | 3.6255608     |
------------

--------------------------------------
| approxkl           | 0.00014769535 |
| clipfrac           | 0.000859375   |
| explained_variance | -8.5          |
| fps                | 1105          |
| n_updates          | 1536          |
| policy_entropy     | 0.153931      |
| policy_loss        | -0.0007192367 |
| serial_timesteps   | 4915200       |
| time_elapsed       | 4.92e+03      |
| total_timesteps    | 4915200       |
| value_loss         | 0.37807006    |
--------------------------------------
--------------------------------------
| approxkl           | 0.00025103166 |
| clipfrac           | 0.0028125     |
| explained_variance | 0.967         |
| fps                | 1100          |
| n_updates          | 1537          |
| policy_entropy     | 0.08893759    |
| policy_loss        | 0.00018299297 |
| serial_timesteps   | 4918400       |
| time_elapsed       | 4.93e+03      |
| total_timesteps    | 4918400       |
| value_loss         | 3.7979023     |
-------------------------

-------------------------------------
| approxkl           | 0.0026159578 |
| clipfrac           | 0.0171875    |
| explained_variance | -2.92        |
| fps                | 1082         |
| n_updates          | 1553         |
| policy_entropy     | 0.14190838   |
| policy_loss        | -0.001053312 |
| serial_timesteps   | 4969600      |
| time_elapsed       | 4.97e+03     |
| total_timesteps    | 4969600      |
| value_loss         | 0.11880896   |
-------------------------------------
--------------------------------------
| approxkl           | 0.00059405674 |
| clipfrac           | 0.005703125   |
| explained_variance | 0.957         |
| fps                | 1091          |
| n_updates          | 1554          |
| policy_entropy     | 0.11757274    |
| policy_loss        | 0.00015027083 |
| serial_timesteps   | 4972800       |
| time_elapsed       | 4.98e+03      |
| total_timesteps    | 4972800       |
| value_loss         | 2.927855      |
--------------------------------------

## Testing lesson1

In [85]:
# model_lesson1 = PPO2.load(model_names[1])
test(env_lesson1, model_lesson1, render = True, total=20)

Episode 0 finished
Episode 1 finished
Episode 2 finished
Episode 3 finished
Episode 4 finished
Episode 5 finished
Episode 6 finished
Episode 7 finished
Episode 8 finished
Episode 9 finished
Episode 10 finished
Episode 11 finished
Episode 12 finished
Episode 13 finished
Episode 14 finished
Episode 15 finished
Episode 16 finished
Episode 17 finished
Episode 18 finished
Episode 19 finished
Win  20 / 20  games
Tie  0 / 20  games
Lose  0 / 20  games


## Training lesson 2
### 11x11 grid with 8 wooden boxes

In [60]:
config_lesson2 = wood_box_lesson2_env()
env_lesson2 = initialize_env(config_lesson2)

In [61]:
# model_lesson1 = PPO2.load(load_path = model_names[1],
#                           tensorboard_log = "./ppo2_pommerman_box_collect_tensorboard/")
model_lesson2 = train(model_name = model_names[2], 
                      model = model_lesson1,
                      env = env_lesson2, 
                      n_steps = n_steps, 
                      total_timesteps = total_timestep)
# model_lesson2.save(model_names[2])

--------------------------------------
| approxkl           | 4.3879052e-05 |
| clipfrac           | 0.0           |
| explained_variance | 0.929         |
| fps                | 1137          |
| n_updates          | 1             |
| policy_entropy     | 0.12292739    |
| policy_loss        | 3.6404278e-06 |
| serial_timesteps   | 3200          |
| time_elapsed       | 2.15e-06      |
| total_timesteps    | 3200          |
| value_loss         | 3.5194335     |
--------------------------------------
---------------------------------------
| approxkl           | 5.3898133e-05  |
| clipfrac           | 0.0003125      |
| explained_variance | 0.847          |
| fps                | 1179           |
| n_updates          | 2              |
| policy_entropy     | 0.13614        |
| policy_loss        | -0.00018177349 |
| serial_timesteps   | 6400           |
| time_elapsed       | 2.83           |
| total_timesteps    | 6400           |
| value_loss         | 8.935968       |
-------------

-------------------------------------
| approxkl           | 0.0017518915 |
| clipfrac           | 0.016640626  |
| explained_variance | 0.847        |
| fps                | 1091         |
| n_updates          | 18           |
| policy_entropy     | 0.18273216   |
| policy_loss        | -0.000776406 |
| serial_timesteps   | 57600        |
| time_elapsed       | 48.5         |
| total_timesteps    | 57600        |
| value_loss         | 4.6277075    |
-------------------------------------
---------------------------------------
| approxkl           | 0.00018387841  |
| clipfrac           | 0.00140625     |
| explained_variance | 0.951          |
| fps                | 1160           |
| n_updates          | 19             |
| policy_entropy     | 0.07635873     |
| policy_loss        | -2.4388362e-05 |
| serial_timesteps   | 60800          |
| time_elapsed       | 51.5           |
| total_timesteps    | 60800          |
| value_loss         | 4.8112736      |
--------------------------

--------------------------------------
| approxkl           | 5.6442505e-06 |
| clipfrac           | 0.0           |
| explained_variance | 0.901         |
| fps                | 1203          |
| n_updates          | 35            |
| policy_entropy     | 0.06712589    |
| policy_loss        | 3.3569486e-05 |
| serial_timesteps   | 112000        |
| time_elapsed       | 97.1          |
| total_timesteps    | 112000        |
| value_loss         | 8.173052      |
--------------------------------------
--------------------------------------
| approxkl           | 1.8778277e-05 |
| clipfrac           | 0.0           |
| explained_variance | 0.904         |
| fps                | 1134          |
| n_updates          | 36            |
| policy_entropy     | 0.11758936    |
| policy_loss        | -3.133729e-05 |
| serial_timesteps   | 115200        |
| time_elapsed       | 99.7          |
| total_timesteps    | 115200        |
| value_loss         | 4.0196047     |
-------------------------

--------------------------------------
| approxkl           | 2.5123958e-05 |
| clipfrac           | 0.0           |
| explained_variance | 0.911         |
| fps                | 1065          |
| n_updates          | 51            |
| policy_entropy     | 0.16356662    |
| policy_loss        | 7.882886e-05  |
| serial_timesteps   | 163200        |
| time_elapsed       | 142           |
| total_timesteps    | 163200        |
| value_loss         | 8.583174      |
--------------------------------------
--------------------------------------
| approxkl           | 9.908534e-06  |
| clipfrac           | 0.0           |
| explained_variance | 0.953         |
| fps                | 1012          |
| n_updates          | 52            |
| policy_entropy     | 0.07980837    |
| policy_loss        | -7.385791e-05 |
| serial_timesteps   | 166400        |
| time_elapsed       | 145           |
| total_timesteps    | 166400        |
| value_loss         | 5.535645      |
-------------------------

---------------------------------------
| approxkl           | 7.3347096e-06  |
| clipfrac           | 0.0            |
| explained_variance | 0.92           |
| fps                | 1132           |
| n_updates          | 68             |
| policy_entropy     | 0.084151104    |
| policy_loss        | -2.7946346e-05 |
| serial_timesteps   | 217600         |
| time_elapsed       | 194            |
| total_timesteps    | 217600         |
| value_loss         | 6.6775417      |
---------------------------------------
---------------------------------------
| approxkl           | 1.3396701e-05  |
| clipfrac           | 0.0            |
| explained_variance | 0.938          |
| fps                | 1105           |
| n_updates          | 69             |
| policy_entropy     | 0.11674805     |
| policy_loss        | -5.5667086e-05 |
| serial_timesteps   | 220800         |
| time_elapsed       | 197            |
| total_timesteps    | 220800         |
| value_loss         | 3.5916903      |


...

---------------------------------------
| approxkl           | 0.00025580236  |
| clipfrac           | 0.0015625      |
| explained_variance | 0.947          |
| fps                | 964            |
| n_updates          | 1487           |
| policy_entropy     | 0.17512608     |
| policy_loss        | -0.00026815018 |
| serial_timesteps   | 4758400        |
| time_elapsed       | 8.25e+03       |
| total_timesteps    | 4758400        |
| value_loss         | 1.8232782      |
---------------------------------------
--------------------------------------
| approxkl           | 0.0001547979  |
| clipfrac           | 0.000859375   |
| explained_variance | 0.818         |
| fps                | 1030          |
| n_updates          | 1488          |
| policy_entropy     | 0.096240446   |
| policy_loss        | 0.00014192291 |
| serial_timesteps   | 4761600       |
| time_elapsed       | 8.25e+03      |
| total_timesteps    | 4761600       |
| value_loss         | 12.590279     |
------------

--------------------------------------
| approxkl           | 0.00030831143 |
| clipfrac           | 0.0075        |
| explained_variance | 0.918         |
| fps                | 965           |
| n_updates          | 1504          |
| policy_entropy     | 0.20607191    |
| policy_loss        | 0.00012833222 |
| serial_timesteps   | 4812800       |
| time_elapsed       | 8.3e+03       |
| total_timesteps    | 4812800       |
| value_loss         | 6.6864214     |
--------------------------------------
--------------------------------------
| approxkl           | 0.0016886992  |
| clipfrac           | 0.02265625    |
| explained_variance | -0.309        |
| fps                | 927           |
| n_updates          | 1505          |
| policy_entropy     | 0.23873669    |
| policy_loss        | -0.0019344632 |
| serial_timesteps   | 4816000       |
| time_elapsed       | 8.3e+03       |
| total_timesteps    | 4816000       |
| value_loss         | 0.0910907     |
-------------------------

---------------------------------------
| approxkl           | 0.00033988844  |
| clipfrac           | 0.00046875002  |
| explained_variance | 0.944          |
| fps                | 940            |
| n_updates          | 1521           |
| policy_entropy     | 0.23065445     |
| policy_loss        | -0.00050101825 |
| serial_timesteps   | 4867200        |
| time_elapsed       | 8.36e+03       |
| total_timesteps    | 4867200        |
| value_loss         | 3.2020836      |
---------------------------------------
--------------------------------------
| approxkl           | 0.00074767385 |
| clipfrac           | 0.0           |
| explained_variance | 0.962         |
| fps                | 954           |
| n_updates          | 1522          |
| policy_entropy     | 0.32902268    |
| policy_loss        | 0.00038941822 |
| serial_timesteps   | 4870400       |
| time_elapsed       | 8.36e+03      |
| total_timesteps    | 4870400       |
| value_loss         | 2.7852516     |
------------

---------------------------------------
| approxkl           | 0.00017607506  |
| clipfrac           | 0.0009375      |
| explained_variance | 0.965          |
| fps                | 908            |
| n_updates          | 1538           |
| policy_entropy     | 0.24515241     |
| policy_loss        | -6.5764485e-05 |
| serial_timesteps   | 4921600        |
| time_elapsed       | 8.42e+03       |
| total_timesteps    | 4921600        |
| value_loss         | 2.7747092      |
---------------------------------------
--------------------------------------
| approxkl           | 0.00010434107 |
| clipfrac           | 0.000625      |
| explained_variance | 0.94          |
| fps                | 927           |
| n_updates          | 1539          |
| policy_entropy     | 0.14056572    |
| policy_loss        | 9.3327464e-05 |
| serial_timesteps   | 4924800       |
| time_elapsed       | 8.42e+03      |
| total_timesteps    | 4924800       |
| value_loss         | 3.53937       |
------------

--------------------------------------
| approxkl           | 0.00046723563 |
| clipfrac           | 0.004921875   |
| explained_variance | 0.955         |
| fps                | 1017          |
| n_updates          | 1555          |
| policy_entropy     | 0.16191944    |
| policy_loss        | 0.00035953455 |
| serial_timesteps   | 4976000       |
| time_elapsed       | 8.47e+03      |
| total_timesteps    | 4976000       |
| value_loss         | 2.9802845     |
--------------------------------------
--------------------------------------
| approxkl           | 0.00020537365 |
| clipfrac           | 0.001484375   |
| explained_variance | 0.96          |
| fps                | 987           |
| n_updates          | 1556          |
| policy_entropy     | 0.17365478    |
| policy_loss        | 0.00013790402 |
| serial_timesteps   | 4979200       |
| time_elapsed       | 8.48e+03      |
| total_timesteps    | 4979200       |
| value_loss         | 2.3416784     |
-------------------------

## Testing lesson2

In [62]:
# model_lesson2 = PPO2.load(model_names[2])
test(env_lesson2, model_lesson2, render = False)

Episode 0 finished
Episode 1 finished
Episode 2 finished
Episode 3 finished
Episode 4 finished
Episode 5 finished
Episode 6 finished
Episode 7 finished
Episode 8 finished
Episode 9 finished
Episode 10 finished
Episode 11 finished
Episode 12 finished
Episode 13 finished
Episode 14 finished
Episode 15 finished
Episode 16 finished
Episode 17 finished
Episode 18 finished
Episode 19 finished
Episode 20 finished
Episode 21 finished
Episode 22 finished
Episode 23 finished
Episode 24 finished
Episode 25 finished
Episode 26 finished
Episode 27 finished
Episode 28 finished
Episode 29 finished
Episode 30 finished
Episode 31 finished
Episode 32 finished
Episode 33 finished
Episode 34 finished
Episode 35 finished
Episode 36 finished
Episode 37 finished
Episode 38 finished
Episode 39 finished
Episode 40 finished
Episode 41 finished
Episode 42 finished
Episode 43 finished
Episode 44 finished
Episode 45 finished
Episode 46 finished
Episode 47 finished
Episode 48 finished
Episode 49 finished
Episode 50

## Training lesson 3
### 11x11 grid with 16 wooden boxes

In [63]:
config_lesson3 = wood_box_lesson3_env()
env_lesson3 = initialize_env(config_lesson3)

In [64]:
# model_lesson2 = PPO2.load(load_path = model_names[2],
#                           tensorboard_log = "./ppo2_pommerman_box_collect_tensorboard/")
model_lesson3 = train(model_name = model_names[3], 
                      model = model_lesson2,
                      env = env_lesson3, 
                      n_steps = n_steps, 
                      total_timesteps = total_timestep)
# model_lesson3.save(model_names[3])

---------------------------------------
| approxkl           | 2.500835e-05   |
| clipfrac           | 0.0            |
| explained_variance | 0.907          |
| fps                | 904            |
| n_updates          | 1              |
| policy_entropy     | 0.1448917      |
| policy_loss        | -0.00012760595 |
| serial_timesteps   | 3200           |
| time_elapsed       | 3.1e-06        |
| total_timesteps    | 3200           |
| value_loss         | 6.008588       |
---------------------------------------
--------------------------------------
| approxkl           | 2.6183472e-05 |
| clipfrac           | 0.0           |
| explained_variance | 0.901         |
| fps                | 961           |
| n_updates          | 2             |
| policy_entropy     | 0.18287149    |
| policy_loss        | -7.895529e-06 |
| serial_timesteps   | 6400          |
| time_elapsed       | 3.55          |
| total_timesteps    | 6400          |
| value_loss         | 7.947686      |
------------

--------------------------------------
| approxkl           | 4.4999426e-05 |
| clipfrac           | 0.0           |
| explained_variance | 0.946         |
| fps                | 963           |
| n_updates          | 18            |
| policy_entropy     | 0.17021397    |
| policy_loss        | -8.312609e-07 |
| serial_timesteps   | 57600         |
| time_elapsed       | 58            |
| total_timesteps    | 57600         |
| value_loss         | 5.6312056     |
--------------------------------------
---------------------------------------
| approxkl           | 2.2625416e-05  |
| clipfrac           | 0.0            |
| explained_variance | 0.879          |
| fps                | 961            |
| n_updates          | 19             |
| policy_entropy     | 0.119366266    |
| policy_loss        | -8.1411075e-05 |
| serial_timesteps   | 60800          |
| time_elapsed       | 61.3           |
| total_timesteps    | 60800          |
| value_loss         | 6.163397       |
-------------

---------------------------------------
| approxkl           | 4.7075846e-05  |
| clipfrac           | 7.8125e-05     |
| explained_variance | 0.97           |
| fps                | 953            |
| n_updates          | 35             |
| policy_entropy     | 0.17822075     |
| policy_loss        | -5.0592796e-05 |
| serial_timesteps   | 112000         |
| time_elapsed       | 116            |
| total_timesteps    | 112000         |
| value_loss         | 0.7152832      |
---------------------------------------
--------------------------------------
| approxkl           | 0.00020427935 |
| clipfrac           | 0.003828125   |
| explained_variance | 0.783         |
| fps                | 1016          |
| n_updates          | 36            |
| policy_entropy     | 0.15171184    |
| policy_loss        | 7.714264e-05  |
| serial_timesteps   | 115200        |
| time_elapsed       | 119           |
| total_timesteps    | 115200        |
| value_loss         | 14.238252     |
------------

--------------------------------------
| approxkl           | 1.1485063e-05 |
| clipfrac           | 0.0           |
| explained_variance | 0.936         |
| fps                | 918           |
| n_updates          | 51            |
| policy_entropy     | 0.1287555     |
| policy_loss        | -2.175197e-05 |
| serial_timesteps   | 163200        |
| time_elapsed       | 169           |
| total_timesteps    | 163200        |
| value_loss         | 5.930783      |
--------------------------------------
--------------------------------------
| approxkl           | 3.3510783e-05 |
| clipfrac           | 0.0           |
| explained_variance | 0.932         |
| fps                | 912           |
| n_updates          | 52            |
| policy_entropy     | 0.16318238    |
| policy_loss        | -9.296634e-05 |
| serial_timesteps   | 166400        |
| time_elapsed       | 172           |
| total_timesteps    | 166400        |
| value_loss         | 6.8720345     |
-------------------------

---------------------------------------
| approxkl           | 5.768657e-06   |
| clipfrac           | 0.0            |
| explained_variance | 0.988          |
| fps                | 926            |
| n_updates          | 68             |
| policy_entropy     | 0.22195645     |
| policy_loss        | -1.4221891e-05 |
| serial_timesteps   | 217600         |
| time_elapsed       | 226            |
| total_timesteps    | 217600         |
| value_loss         | 0.65203065     |
---------------------------------------
--------------------------------------
| approxkl           | 8.953664e-05  |
| clipfrac           | 0.0           |
| explained_variance | 0.957         |
| fps                | 931           |
| n_updates          | 69            |
| policy_entropy     | 0.20705326    |
| policy_loss        | -0.0007269458 |
| serial_timesteps   | 220800        |
| time_elapsed       | 229           |
| total_timesteps    | 220800        |
| value_loss         | 2.3517802     |
------------

...

--------------------------------------
| approxkl           | 5.7534606e-05 |
| clipfrac           | 0.00015625    |
| explained_variance | 0.972         |
| fps                | 985           |
| n_updates          | 1483          |
| policy_entropy     | 0.13614455    |
| policy_loss        | 9.1341135e-06 |
| serial_timesteps   | 4745600       |
| time_elapsed       | 4.91e+03      |
| total_timesteps    | 4745600       |
| value_loss         | 4.095364      |
--------------------------------------
--------------------------------------
| approxkl           | 9.3678056e-05 |
| clipfrac           | 0.000234375   |
| explained_variance | 0.972         |
| fps                | 998           |
| n_updates          | 1484          |
| policy_entropy     | 0.17636803    |
| policy_loss        | -6.805912e-05 |
| serial_timesteps   | 4748800       |
| time_elapsed       | 4.91e+03      |
| total_timesteps    | 4748800       |
| value_loss         | 3.924798      |
-------------------------

--------------------------------------
| approxkl           | 4.2925414e-05 |
| clipfrac           | 0.00015625    |
| explained_variance | 0.974         |
| fps                | 939           |
| n_updates          | 1500          |
| policy_entropy     | 0.15847507    |
| policy_loss        | -6.718162e-05 |
| serial_timesteps   | 4800000       |
| time_elapsed       | 4.97e+03      |
| total_timesteps    | 4800000       |
| value_loss         | 3.5272346     |
--------------------------------------
---------------------------------------
| approxkl           | 4.177331e-05   |
| clipfrac           | 0.0            |
| explained_variance | 0.97           |
| fps                | 1035           |
| n_updates          | 1501           |
| policy_entropy     | 0.219242       |
| policy_loss        | -3.9779712e-05 |
| serial_timesteps   | 4803200        |
| time_elapsed       | 4.97e+03       |
| total_timesteps    | 4803200        |
| value_loss         | 2.2239735      |
-------------

---------------------------------------
| approxkl           | 0.00044063738  |
| clipfrac           | 0.004921875    |
| explained_variance | 0.978          |
| fps                | 9              |
| n_updates          | 1516           |
| policy_entropy     | 0.17497782     |
| policy_loss        | -0.00015856221 |
| serial_timesteps   | 4851200        |
| time_elapsed       | 5.34e+03       |
| total_timesteps    | 4851200        |
| value_loss         | 2.8437822      |
---------------------------------------
---------------------------------------
| approxkl           | 0.00097438274  |
| clipfrac           | 0.010234375    |
| explained_variance | 0.968          |
| fps                | 1097           |
| n_updates          | 1517           |
| policy_entropy     | 0.22387877     |
| policy_loss        | -0.00056709046 |
| serial_timesteps   | 4854400        |
| time_elapsed       | 5.66e+03       |
| total_timesteps    | 4854400        |
| value_loss         | 0.31590372     |


---------------------------------------
| approxkl           | 0.00023246     |
| clipfrac           | 0.001484375    |
| explained_variance | -4.96          |
| fps                | 1181           |
| n_updates          | 1532           |
| policy_entropy     | 0.20832174     |
| policy_loss        | -0.00041194676 |
| serial_timesteps   | 4902400        |
| time_elapsed       | 5.73e+03       |
| total_timesteps    | 4902400        |
| value_loss         | 0.61837167     |
---------------------------------------
--------------------------------------
| approxkl           | 0.00025698333 |
| clipfrac           | 0.00171875    |
| explained_variance | 0.965         |
| fps                | 1184          |
| n_updates          | 1533          |
| policy_entropy     | 0.11737829    |
| policy_loss        | -9.867974e-05 |
| serial_timesteps   | 4905600       |
| time_elapsed       | 5.73e+03      |
| total_timesteps    | 4905600       |
| value_loss         | 5.163671      |
------------

--------------------------------------
| approxkl           | 0.00058714155 |
| clipfrac           | 0.00390625    |
| explained_variance | 0.977         |
| fps                | 1139          |
| n_updates          | 1549          |
| policy_entropy     | 0.16881725    |
| policy_loss        | 0.0006411596  |
| serial_timesteps   | 4956800       |
| time_elapsed       | 5.78e+03      |
| total_timesteps    | 4956800       |
| value_loss         | 3.1428747     |
--------------------------------------
-------------------------------------
| approxkl           | 0.000638787  |
| clipfrac           | 0.006328125  |
| explained_variance | 0.951        |
| fps                | 1166         |
| n_updates          | 1550         |
| policy_entropy     | 0.1387732    |
| policy_loss        | 0.0020091622 |
| serial_timesteps   | 4960000      |
| time_elapsed       | 5.78e+03     |
| total_timesteps    | 4960000      |
| value_loss         | 6.2282953    |
-------------------------------------

## Testing lesson3

In [65]:
# model_lesson3 = PPO2.load(model_names[3])
test(env_lesson3, model_lesson3, render = False)

Episode 0 finished
Episode 1 finished
Episode 2 finished
Episode 3 finished
Episode 4 finished
Episode 5 finished
Episode 6 finished
Episode 7 finished
Episode 8 finished
Episode 9 finished
Episode 10 finished
Episode 11 finished
Episode 12 finished
Episode 13 finished
Episode 14 finished
Episode 15 finished
Episode 16 finished
Episode 17 finished
Episode 18 finished
Episode 19 finished
Episode 20 finished
Episode 21 finished
Episode 22 finished
Episode 23 finished
Episode 24 finished
Episode 25 finished
Episode 26 finished
Episode 27 finished
Episode 28 finished
Episode 29 finished
Episode 30 finished
Episode 31 finished
Episode 32 finished
Episode 33 finished
Episode 34 finished
Episode 35 finished
Episode 36 finished
Episode 37 finished
Episode 38 finished
Episode 39 finished
Episode 40 finished
Episode 41 finished
Episode 42 finished
Episode 43 finished
Episode 44 finished
Episode 45 finished
Episode 46 finished
Episode 47 finished
Episode 48 finished
Episode 49 finished
Episode 50

## Training lesson 4
### 11x11 grid with 32 wooden boxes

In [66]:
config_lesson4 = wood_box_lesson4_env()
env_lesson4 = initialize_env(config_lesson4)

In [67]:
# model_lesson3 = PPO2.load(load_path = model_names[3],
#                           tensorboard_log = "./ppo2_pommerman_box_collect_tensorboard/")
model_lesson4 = train(model_name = model_names[4], 
                      model = model_lesson3,
                      env = env_lesson4, 
                      n_steps = n_steps, 
                      total_timesteps = total_timestep)
# model_lesson4.save(model_names[4])

---------------------------------------
| approxkl           | 0.00011778335  |
| clipfrac           | 0.000234375    |
| explained_variance | 0.979          |
| fps                | 1103           |
| n_updates          | 1              |
| policy_entropy     | 0.16538613     |
| policy_loss        | -6.4058455e-05 |
| serial_timesteps   | 3200           |
| time_elapsed       | 1.91e-06       |
| total_timesteps    | 3200           |
| value_loss         | 2.1946805      |
---------------------------------------
---------------------------------------
| approxkl           | 1.4984969e-05  |
| clipfrac           | 0.0            |
| explained_variance | 0.966          |
| fps                | 1112           |
| n_updates          | 2              |
| policy_entropy     | 0.122646004    |
| policy_loss        | -5.7730304e-05 |
| serial_timesteps   | 6400           |
| time_elapsed       | 2.91           |
| total_timesteps    | 6400           |
| value_loss         | 4.0503445      |


--------------------------------------
| approxkl           | 0.003004672   |
| clipfrac           | 0.027265625   |
| explained_variance | -4.53         |
| fps                | 1039          |
| n_updates          | 18            |
| policy_entropy     | 0.21557593    |
| policy_loss        | -0.0006326508 |
| serial_timesteps   | 57600         |
| time_elapsed       | 49.5          |
| total_timesteps    | 57600         |
| value_loss         | 0.2570749     |
--------------------------------------
---------------------------------------
| approxkl           | 0.00011939183  |
| clipfrac           | 0.00093750004  |
| explained_variance | 0.96           |
| fps                | 1104           |
| n_updates          | 19             |
| policy_entropy     | 0.10430935     |
| policy_loss        | -4.8181264e-05 |
| serial_timesteps   | 60800          |
| time_elapsed       | 52.6           |
| total_timesteps    | 60800          |
| value_loss         | 5.2871594      |
-------------

--------------------------------------
| approxkl           | 0.00030216516 |
| clipfrac           | 0.00296875    |
| explained_variance | 0.961         |
| fps                | 1020          |
| n_updates          | 34            |
| policy_entropy     | 0.17954674    |
| policy_loss        | 0.00037518138 |
| serial_timesteps   | 108800        |
| time_elapsed       | 99.8          |
| total_timesteps    | 108800        |
| value_loss         | 3.529798      |
--------------------------------------
--------------------------------------
| approxkl           | 0.00010243518 |
| clipfrac           | 0.00078125    |
| explained_variance | 0.939         |
| fps                | 1036          |
| n_updates          | 35            |
| policy_entropy     | 0.118767835   |
| policy_loss        | 5.1750838e-05 |
| serial_timesteps   | 112000        |
| time_elapsed       | 103           |
| total_timesteps    | 112000        |
| value_loss         | 6.0841074     |
-------------------------

--------------------------------------
| approxkl           | 3.844592e-05  |
| clipfrac           | 7.8125e-05    |
| explained_variance | 0.973         |
| fps                | 878           |
| n_updates          | 51            |
| policy_entropy     | 0.13600591    |
| policy_loss        | -0.0001519391 |
| serial_timesteps   | 163200        |
| time_elapsed       | 149           |
| total_timesteps    | 163200        |
| value_loss         | 3.1163006     |
--------------------------------------
---------------------------------------
| approxkl           | 1.3861432e-05  |
| clipfrac           | 0.0            |
| explained_variance | 0.942          |
| fps                | 750            |
| n_updates          | 52             |
| policy_entropy     | 0.09201777     |
| policy_loss        | -4.5221073e-05 |
| serial_timesteps   | 166400         |
| time_elapsed       | 153            |
| total_timesteps    | 166400         |
| value_loss         | 7.810003       |
-------------

---------------------------------------
| approxkl           | 5.9940226e-07  |
| clipfrac           | 0.0            |
| explained_variance | 0.952          |
| fps                | 918            |
| n_updates          | 67             |
| policy_entropy     | 0.06338045     |
| policy_loss        | -2.5726856e-06 |
| serial_timesteps   | 214400         |
| time_elapsed       | 216            |
| total_timesteps    | 214400         |
| value_loss         | 6.5745707      |
---------------------------------------
---------------------------------------
| approxkl           | 2.6833932e-06  |
| clipfrac           | 0.0            |
| explained_variance | 0.969          |
| fps                | 845            |
| n_updates          | 68             |
| policy_entropy     | 0.1417643      |
| policy_loss        | -1.0418743e-05 |
| serial_timesteps   | 217600         |
| time_elapsed       | 220            |
| total_timesteps    | 217600         |
| value_loss         | 4.166771       |


...

--------------------------------------
| approxkl           | 0.0007728118  |
| clipfrac           | 0.00984375    |
| explained_variance | 0.542         |
| fps                | 912           |
| n_updates          | 1493          |
| policy_entropy     | 0.061881535   |
| policy_loss        | -0.0009722217 |
| serial_timesteps   | 4777600       |
| time_elapsed       | 4.43e+03      |
| total_timesteps    | 4777600       |
| value_loss         | 0.0016064362  |
--------------------------------------
---------------------------------------
| approxkl           | 0.0010818639   |
| clipfrac           | 0.01203125     |
| explained_variance | 0.623          |
| fps                | 912            |
| n_updates          | 1494           |
| policy_entropy     | 0.060824856    |
| policy_loss        | -0.00020238187 |
| serial_timesteps   | 4780800        |
| time_elapsed       | 4.43e+03       |
| total_timesteps    | 4780800        |
| value_loss         | 0.001399658    |
-------------

--------------------------------------
| approxkl           | 0.0005846745  |
| clipfrac           | 0.005078125   |
| explained_variance | 0.527         |
| fps                | 951           |
| n_updates          | 1510          |
| policy_entropy     | 0.05783622    |
| policy_loss        | -0.0022833818 |
| serial_timesteps   | 4832000       |
| time_elapsed       | 4.49e+03      |
| total_timesteps    | 4832000       |
| value_loss         | 0.007938063   |
--------------------------------------
--------------------------------------
| approxkl           | 0.00041265017 |
| clipfrac           | 0.005         |
| explained_variance | 0.538         |
| fps                | 968           |
| n_updates          | 1511          |
| policy_entropy     | 0.052689232   |
| policy_loss        | -0.0014034878 |
| serial_timesteps   | 4835200       |
| time_elapsed       | 4.49e+03      |
| total_timesteps    | 4835200       |
| value_loss         | 0.0036365464  |
-------------------------

--------------------------------------
| approxkl           | 0.0009136405  |
| clipfrac           | 0.007421875   |
| explained_variance | 0.497         |
| fps                | 926           |
| n_updates          | 1527          |
| policy_entropy     | 0.05541466    |
| policy_loss        | -0.0013614912 |
| serial_timesteps   | 4886400       |
| time_elapsed       | 4.54e+03      |
| total_timesteps    | 4886400       |
| value_loss         | 0.0017141802  |
--------------------------------------
--------------------------------------
| approxkl           | 0.00063489017 |
| clipfrac           | 0.005859375   |
| explained_variance | 0.58          |
| fps                | 964           |
| n_updates          | 1528          |
| policy_entropy     | 0.06570767    |
| policy_loss        | -0.0010485931 |
| serial_timesteps   | 4889600       |
| time_elapsed       | 4.55e+03      |
| total_timesteps    | 4889600       |
| value_loss         | 0.0014684252  |
-------------------------

--------------------------------------
| approxkl           | 0.00076337066 |
| clipfrac           | 0.00953125    |
| explained_variance | 0.582         |
| fps                | 1016          |
| n_updates          | 1544          |
| policy_entropy     | 0.052149568   |
| policy_loss        | -0.001023986  |
| serial_timesteps   | 4940800       |
| time_elapsed       | 4.6e+03       |
| total_timesteps    | 4940800       |
| value_loss         | 0.0019041802  |
--------------------------------------
---------------------------------------
| approxkl           | 0.000390436    |
| clipfrac           | 0.0037500001   |
| explained_variance | 0.408          |
| fps                | 965            |
| n_updates          | 1545           |
| policy_entropy     | 0.052502416    |
| policy_loss        | -0.00090688886 |
| serial_timesteps   | 4944000        |
| time_elapsed       | 4.6e+03        |
| total_timesteps    | 4944000        |
| value_loss         | 0.001714992    |
-------------

--------------------------------------
| approxkl           | 0.0009778237  |
| clipfrac           | 0.00671875    |
| explained_variance | 0.616         |
| fps                | 953           |
| n_updates          | 1561          |
| policy_entropy     | 0.06723802    |
| policy_loss        | -0.0011924133 |
| serial_timesteps   | 4995200       |
| time_elapsed       | 4.66e+03      |
| total_timesteps    | 4995200       |
| value_loss         | 0.0012612448  |
--------------------------------------
--------------------------------------
| approxkl           | 0.0013464325  |
| clipfrac           | 0.012578124   |
| explained_variance | 0.594         |
| fps                | 963           |
| n_updates          | 1562          |
| policy_entropy     | 0.06887908    |
| policy_loss        | -0.0013013791 |
| serial_timesteps   | 4998400       |
| time_elapsed       | 4.66e+03      |
| total_timesteps    | 4998400       |
| value_loss         | 0.0013350414  |
-------------------------

## Testing lesson4

In [68]:
# model_lesson4 = PPO2.load(model_names[4])
test(env_lesson4, model_lesson4, render = False)

Episode 0 finished
Episode 1 finished
Episode 2 finished
Episode 3 finished
Episode 4 finished
Episode 5 finished
Episode 6 finished
Episode 7 finished
Episode 8 finished
Episode 9 finished
Episode 10 finished
Episode 11 finished
Episode 12 finished
Episode 13 finished
Episode 14 finished
Episode 15 finished
Episode 16 finished
Episode 17 finished
Episode 18 finished
Episode 19 finished
Episode 20 finished
Episode 21 finished
Episode 22 finished
Episode 23 finished
Episode 24 finished
Episode 25 finished
Episode 26 finished
Episode 27 finished
Episode 28 finished
Episode 29 finished
Episode 30 finished
Episode 31 finished
Episode 32 finished
Episode 33 finished
Episode 34 finished
Episode 35 finished
Episode 36 finished
Episode 37 finished
Episode 38 finished
Episode 39 finished
Episode 40 finished
Episode 41 finished
Episode 42 finished
Episode 43 finished
Episode 44 finished
Episode 45 finished
Episode 46 finished
Episode 47 finished
Episode 48 finished
Episode 49 finished
Episode 50

## Training lesson 5
### 11x11 grid with 64 wooden boxes

In [69]:
config_lesson5 = wood_box_lesson5_env()
env_lesson5 = initialize_env(config_lesson5)

In [70]:
# model_lesson4 = PPO2.load(load_path = model_names[4],
#                           tensorboard_log = "./ppo2_pommerman_box_collect_tensorboard/")
model_lesson5 = train(model_name = model_names[5], 
                      model = model_lesson4,
                      env = env_lesson5, 
                      n_steps = n_steps, 
                      total_timesteps = total_timestep)


--------------------------------------
| approxkl           | 0.0009848711  |
| clipfrac           | 0.009921875   |
| explained_variance | 0.68          |
| fps                | 898           |
| n_updates          | 1             |
| policy_entropy     | 0.075007915   |
| policy_loss        | -0.0009413279 |
| serial_timesteps   | 3200          |
| time_elapsed       | 3.1e-06       |
| total_timesteps    | 3200          |
| value_loss         | 0.0010606942  |
--------------------------------------
--------------------------------------
| approxkl           | 0.0010833209  |
| clipfrac           | 0.01203125    |
| explained_variance | 0.657         |
| fps                | 867           |
| n_updates          | 2             |
| policy_entropy     | 0.0730928     |
| policy_loss        | -0.0014716615 |
| serial_timesteps   | 6400          |
| time_elapsed       | 3.57          |
| total_timesteps    | 6400          |
| value_loss         | 0.0010748311  |
-------------------------

--------------------------------------
| approxkl           | 0.0011965457  |
| clipfrac           | 0.011015625   |
| explained_variance | 0.344         |
| fps                | 933           |
| n_updates          | 18            |
| policy_entropy     | 0.07257196    |
| policy_loss        | -0.0023744907 |
| serial_timesteps   | 57600         |
| time_elapsed       | 58.5          |
| total_timesteps    | 57600         |
| value_loss         | 0.0017274539  |
--------------------------------------
--------------------------------------
| approxkl           | 0.00316277    |
| clipfrac           | 0.026562499   |
| explained_variance | 0.591         |
| fps                | 939           |
| n_updates          | 19            |
| policy_entropy     | 0.07365044    |
| policy_loss        | -0.0010087532 |
| serial_timesteps   | 60800         |
| time_elapsed       | 62            |
| total_timesteps    | 60800         |
| value_loss         | 0.005554967   |
-------------------------

--------------------------------------
| approxkl           | 0.0006782301  |
| clipfrac           | 0.0065625003  |
| explained_variance | 0.567         |
| fps                | 915           |
| n_updates          | 35            |
| policy_entropy     | 0.07740382    |
| policy_loss        | -0.0011141188 |
| serial_timesteps   | 112000        |
| time_elapsed       | 119           |
| total_timesteps    | 112000        |
| value_loss         | 0.0014454821  |
--------------------------------------
--------------------------------------
| approxkl           | 0.0011731493  |
| clipfrac           | 0.013203125   |
| explained_variance | 0.0675        |
| fps                | 945           |
| n_updates          | 36            |
| policy_entropy     | 0.08587828    |
| policy_loss        | -0.0016519896 |
| serial_timesteps   | 115200        |
| time_elapsed       | 122           |
| total_timesteps    | 115200        |
| value_loss         | 0.00300695    |
-------------------------

--------------------------------------
| approxkl           | 0.00046118506 |
| clipfrac           | 0.005390625   |
| explained_variance | 0.423         |
| fps                | 952           |
| n_updates          | 52            |
| policy_entropy     | 0.07415887    |
| policy_loss        | -0.0009648249 |
| serial_timesteps   | 166400        |
| time_elapsed       | 178           |
| total_timesteps    | 166400        |
| value_loss         | 0.001977024   |
--------------------------------------
--------------------------------------
| approxkl           | 0.00051443774 |
| clipfrac           | 0.00578125    |
| explained_variance | 0.424         |
| fps                | 964           |
| n_updates          | 53            |
| policy_entropy     | 0.07077193    |
| policy_loss        | -0.0011574766 |
| serial_timesteps   | 169600        |
| time_elapsed       | 181           |
| total_timesteps    | 169600        |
| value_loss         | 0.0016949459  |
-------------------------

--------------------------------------
| approxkl           | 0.0023930995  |
| clipfrac           | 0.024296876   |
| explained_variance | 0.54          |
| fps                | 959           |
| n_updates          | 69            |
| policy_entropy     | 0.072768256   |
| policy_loss        | -0.0007463481 |
| serial_timesteps   | 220800        |
| time_elapsed       | 234           |
| total_timesteps    | 220800        |
| value_loss         | 0.001512497   |
--------------------------------------
--------------------------------------
| approxkl           | 0.0009605742  |
| clipfrac           | 0.013046876   |
| explained_variance | 0.698         |
| fps                | 929           |
| n_updates          | 70            |
| policy_entropy     | 0.11086406    |
| policy_loss        | 0.00065442035 |
| serial_timesteps   | 224000        |
| time_elapsed       | 237           |
| total_timesteps    | 224000        |
| value_loss         | 5.5939546     |
-------------------------

...

--------------------------------------
| approxkl           | 0.0012658963  |
| clipfrac           | 0.01109375    |
| explained_variance | 0.299         |
| fps                | 879           |
| n_updates          | 1480          |
| policy_entropy     | 0.05784855    |
| policy_loss        | -0.0021344023 |
| serial_timesteps   | 4736000       |
| time_elapsed       | 4.53e+03      |
| total_timesteps    | 4736000       |
| value_loss         | 0.007509286   |
--------------------------------------
--------------------------------------
| approxkl           | 0.0002853623  |
| clipfrac           | 0.003671875   |
| explained_variance | 0.701         |
| fps                | 1013          |
| n_updates          | 1481          |
| policy_entropy     | 0.051936988   |
| policy_loss        | -0.0006634181 |
| serial_timesteps   | 4739200       |
| time_elapsed       | 4.53e+03      |
| total_timesteps    | 4739200       |
| value_loss         | 0.0009014852  |
-------------------------

--------------------------------------
| approxkl           | 0.0019190016  |
| clipfrac           | 0.013515625   |
| explained_variance | 0.638         |
| fps                | 1012          |
| n_updates          | 1497          |
| policy_entropy     | 0.065653466   |
| policy_loss        | -0.0011401951 |
| serial_timesteps   | 4790400       |
| time_elapsed       | 4.58e+03      |
| total_timesteps    | 4790400       |
| value_loss         | 0.0009052369  |
--------------------------------------
--------------------------------------
| approxkl           | 0.0021337625  |
| clipfrac           | 0.016640624   |
| explained_variance | 0.677         |
| fps                | 919           |
| n_updates          | 1498          |
| policy_entropy     | 0.07104121    |
| policy_loss        | -0.0016622843 |
| serial_timesteps   | 4793600       |
| time_elapsed       | 4.59e+03      |
| total_timesteps    | 4793600       |
| value_loss         | 0.0008169988  |
-------------------------

---------------------------------------
| approxkl           | 0.00081642356  |
| clipfrac           | 0.006953125    |
| explained_variance | -0.00783       |
| fps                | 946            |
| n_updates          | 1514           |
| policy_entropy     | 0.07298763     |
| policy_loss        | -0.00067769457 |
| serial_timesteps   | 4844800        |
| time_elapsed       | 4.64e+03       |
| total_timesteps    | 4844800        |
| value_loss         | 0.002345271    |
---------------------------------------
--------------------------------------
| approxkl           | 0.002078819   |
| clipfrac           | 0.018437501   |
| explained_variance | 0.324         |
| fps                | 968           |
| n_updates          | 1515          |
| policy_entropy     | 0.069484696   |
| policy_loss        | -0.0013102196 |
| serial_timesteps   | 4848000       |
| time_elapsed       | 4.65e+03      |
| total_timesteps    | 4848000       |
| value_loss         | 0.0019535169  |
------------

---------------------------------------
| approxkl           | 0.0020784016   |
| clipfrac           | 0.021484375    |
| explained_variance | 0.676          |
| fps                | 1167           |
| n_updates          | 1531           |
| policy_entropy     | 0.07045511     |
| policy_loss        | -0.00062763534 |
| serial_timesteps   | 4899200        |
| time_elapsed       | 4.69e+03       |
| total_timesteps    | 4899200        |
| value_loss         | 0.0007966877   |
---------------------------------------
--------------------------------------
| approxkl           | 0.0009899     |
| clipfrac           | 0.008125      |
| explained_variance | 0.662         |
| fps                | 1184          |
| n_updates          | 1532          |
| policy_entropy     | 0.06509351    |
| policy_loss        | -0.0010804622 |
| serial_timesteps   | 4902400       |
| time_elapsed       | 4.7e+03       |
| total_timesteps    | 4902400       |
| value_loss         | 0.0008623192  |
------------

--------------------------------------
| approxkl           | 0.0012108323  |
| clipfrac           | 0.01234375    |
| explained_variance | 0.636         |
| fps                | 1121          |
| n_updates          | 1548          |
| policy_entropy     | 0.04988206    |
| policy_loss        | -0.0015576635 |
| serial_timesteps   | 4953600       |
| time_elapsed       | 4.74e+03      |
| total_timesteps    | 4953600       |
| value_loss         | 0.0026686706  |
--------------------------------------
--------------------------------------
| approxkl           | 0.0008242439  |
| clipfrac           | 0.00921875    |
| explained_variance | 0.696         |
| fps                | 1144          |
| n_updates          | 1549          |
| policy_entropy     | 0.047899596   |
| policy_loss        | -0.0009869216 |
| serial_timesteps   | 4956800       |
| time_elapsed       | 4.75e+03      |
| total_timesteps    | 4956800       |
| value_loss         | 0.0007848902  |
-------------------------

In [80]:
# model_lesson5.save(model_names[5])

## Testing lesson5

In [86]:
# model_lesson5 = PPO2.load(model_names[5])
test(env_lesson5, model_lesson5, render = False)

Episode 0 finished
Episode 1 finished
Episode 2 finished
Episode 3 finished
Episode 4 finished
Win  5 / 5  games
Tie  0 / 5  games
Lose  0 / 5  games


In [ ]:
model_lesson5.save(model_names[5])